In [1]:
!pip install --upgrade requests branca six jinja2 numpy chardet idna urllib3 certifi MarkupSafe
!conda install -c conda-forge folium --yes
!conda install -c conda-forge geopy --yes
!pip install bs4
!pip install uszipcode
!pip install tqdm
!pip install git+https://github.com/psychemedia/ipython_magic_folium.git

#import all the libraries
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
import requests
import random
from sklearn.cluster import KMeans
from pandas.io.json import json_normalize
import folium
from geopy.geocoders import Nominatim
import json
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn import metrics
from PIL import Image
import matplotlib.patches as mpatches
import warnings
warnings.filterwarnings("ignore")
import types
from botocore.client import Config
import ibm_boto3
from bs4 import BeautifulSoup
from uszipcode import SearchEngine
import geopy
from geopy.extra.rate_limiter import RateLimiter
import tqdm
from tqdm._tqdm_notebook import tqdm_notebook
%load_ext folium_magic

print('Libraries imported')

Requirement already up-to-date: requests in /opt/conda/envs/Python36/lib/python3.6/site-packages (2.24.0)
Requirement already up-to-date: branca in /opt/conda/envs/Python36/lib/python3.6/site-packages (0.4.1)
Requirement already up-to-date: six in /opt/conda/envs/Python36/lib/python3.6/site-packages (1.15.0)
Requirement already up-to-date: jinja2 in /opt/conda/envs/Python36/lib/python3.6/site-packages (2.11.2)
Requirement already up-to-date: numpy in /opt/conda/envs/Python36/lib/python3.6/site-packages (1.19.1)
Requirement already up-to-date: chardet in /opt/conda/envs/Python36/lib/python3.6/site-packages (3.0.4)
Requirement already up-to-date: idna in /opt/conda/envs/Python36/lib/python3.6/site-packages (2.10)
Requirement already up-to-date: urllib3 in /opt/conda/envs/Python36/lib/python3.6/site-packages (1.25.10)
Requirement already up-to-date: certifi in /opt/conda/envs/Python36/lib/python3.6/site-packages (2020.6.20)
Requirement already up-to-date: MarkupSafe in /opt/conda/envs/Pyt

     |████████████████████████████████| 14.8MB 6.3MB/s eta 0:00:01███████▏  | 13.4MB 6.3MB/s eta 0:00:01
     |████████████████████████████████| 102kB 13.8MB/s ta 0:00:01
  Stored in directory: /home/dsxuser/.tmp/pip-ephem-wheel-cache-38hf0ync/wheels/7c/49/f8/8577b6d1b8fcaa766dd7c6f7996f22a913e4a260443e75a095
Successfully built ipython-magic-folium
Libraries imported


In [58]:


#New York Geographical Data on Neighborhoods/Boroughs
!wget -q -O 'newyork_data.json' https://cocl.us/new_york_dataset
print('Data downloaded!')

#Load data
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)
    

#Examine the relevant data in the features key, which is basically a list of neighborhoods
NY_data = newyork_data['features']

# Transform the NY Data into a Pandas dataframe
# define the dataframe columns
column_names = ['Borough', 'Neighborhood', 'Latitude', 'Longitude'] 

# instantiate the dataframe
NYdf = pd.DataFrame(columns=column_names)

# Make sure the columns properly titled
NYdf
NY_data[0]

for data in NY_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    NYdf = NYdf.append({'Borough': borough,
                        'Neighborhood': neighborhood_name,
                        'Latitude': neighborhood_lat,
                        'Longitude': neighborhood_lon}, ignore_index=True)
    
    #Take only the neighborhoods from Manhattan
NYdf =NYdf[NYdf['Borough'] == 'Manhattan'].reset_index(drop=True)
NYdf.head(10)

Data downloaded!


Borough        Neighborhood   Latitude  Longitude
0  Manhattan         Marble Hill  40.876551 -73.910660
1  Manhattan           Chinatown  40.715618 -73.994279
2  Manhattan  Washington Heights  40.851903 -73.936900
3  Manhattan              Inwood  40.867684 -73.921210
4  Manhattan    Hamilton Heights  40.823604 -73.949688
5  Manhattan      Manhattanville  40.816934 -73.957385
6  Manhattan      Central Harlem  40.815976 -73.943211
7  Manhattan         East Harlem  40.792249 -73.944182
8  Manhattan     Upper East Side  40.775639 -73.960508
9  Manhattan           Yorkville  40.775930 -73.947118

In [59]:
NYdf.shape

(40, 4)

In [60]:
#Prepare NY Map data
NYaddress = 'Columbia University, New York City'

geolocator = Nominatim(user_agent="ny_explorer")
NYlocation = geolocator.geocode(NYaddress)
NYlatitude = NYlocation.latitude
NYlongitude = NYlocation.longitude
print('The geograpical coordinate of Columbia University are {}, {}.'.format(NYlatitude, NYlongitude))

The geograpical coordinate of Columbia University are 40.8079488, -73.96179735775709.


In [61]:
#Visualize Data to ensure it is right as rain
NYdf

Borough         Neighborhood   Latitude  Longitude
0   Manhattan          Marble Hill  40.876551 -73.910660
1   Manhattan            Chinatown  40.715618 -73.994279
2   Manhattan   Washington Heights  40.851903 -73.936900
3   Manhattan               Inwood  40.867684 -73.921210
4   Manhattan     Hamilton Heights  40.823604 -73.949688
5   Manhattan       Manhattanville  40.816934 -73.957385
6   Manhattan       Central Harlem  40.815976 -73.943211
7   Manhattan          East Harlem  40.792249 -73.944182
8   Manhattan      Upper East Side  40.775639 -73.960508
9   Manhattan            Yorkville  40.775930 -73.947118
10  Manhattan           Lenox Hill  40.768113 -73.958860
11  Manhattan     Roosevelt Island  40.762160 -73.949168
12  Manhattan      Upper West Side  40.787658 -73.977059
13  Manhattan       Lincoln Square  40.773529 -73.985338
14  Manhattan              Clinton  40.759101 -73.996119
15  Manhattan              Midtown  40.754691 -73.981669
16  Manhattan          Murray Hill  40.748303 -73.978332
17  Manhattan              Chelsea  40.744035 -74.003116
18  Manhattan    Greenwich Village  40.726933 -73.999914
19  Manhattan         East Village  40.727847 -73.982226
20  Manhattan      Lower East Side  40.717807 -73.980890
21  Manhattan              Tribeca  40.721522 -74.010683
22  Manhattan         Little Italy  40.719324 -73.997305
23  Manhattan                 Soho  40.722184 -74.000657
24  Manhattan         West Village  40.734434 -74.006180
25  Manhattan     Manhattan Valley  40.797307 -73.964286
26  Manhattan  Morningside Heights  40.808000 -73.963896
27  Manhattan             Gramercy  40.737210 -73.981376
28  Manhattan    Battery Park City  40.711932 -74.016869
29  Manhattan   Financial District  40.707107 -74.010665
30  Manhattan        Carnegie Hill  40.782683 -73.953256
31  Manhattan                 Noho  40.723259 -73.988434
32  Manhattan         Civic Center  40.715229 -74.005415
33  Manhattan        Midtown South  40.748510 -73.988713
34  Manhattan         Sutton Place  40.760280 -73.963556
35  Manhattan           Turtle Bay  40.752042 -73.967708
36  Manhattan           Tudor City  40.746917 -73.971219
37  Manhattan      Stuyvesant Town  40.731000 -73.974052
38  Manhattan             Flatiron  40.739673 -73.990947
39  Manhattan         Hudson Yards  40.756658 -74.000111

In [62]:
#From article on best locations to live If you're enrolled in Columbia
rows=['Upper West Side', 'Morningside Heights', 'East Harlem', 'Central Harlem','Hamilton Heights', 'Manhattanville', 'Midtown', ]
  

# selecting rows based on condition 
NY_df = NYdf[NYdf['Neighborhood'].isin(rows)]

#Add Columbia University for mapping purposes

NY_df= NY_df.append({'Borough' : 'Manhattan', 'Neighborhood' : 'Columbia University', 'Latitude' : NYlatitude ,'Longitude' : NYlongitude } , ignore_index=True)

#View dataframe to confirm reduced neighborhoods
NY_df


Borough         Neighborhood   Latitude  Longitude
0  Manhattan     Hamilton Heights  40.823604 -73.949688
1  Manhattan       Manhattanville  40.816934 -73.957385
2  Manhattan       Central Harlem  40.815976 -73.943211
3  Manhattan          East Harlem  40.792249 -73.944182
4  Manhattan      Upper West Side  40.787658 -73.977059
5  Manhattan              Midtown  40.754691 -73.981669
6  Manhattan  Morningside Heights  40.808000 -73.963896
7  Manhattan  Columbia University  40.807949 -73.961797

In [63]:
#Map NY


map_NY = folium.Map(location=[NYlatitude, NYlongitude], zoom_start=12, width='100%', height='100%')

for lat, lng, borough, neighborhood in zip(NY_df['Latitude'], NY_df['Longitude'], NY_df['Borough'], NY_df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_NY)
        
    if  lat == NYlatitude and lng == NYlongitude :
        label = "Columbia University   "+'{},{}'.format(NYlatitude, NYlongitude)
        folium.CircleMarker(
        [NYlatitude, NYlongitude],
        radius=5,
        popup=label,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.5).add_to(map_NY)
       
    
map_NY

In [64]:
from geopy import distance

for  nylat_df, nylng_df, neighborhood in zip( NY_df['Latitude'], NY_df['Longitude'], NY_df['Neighborhood']):
    Columbia = (NYlatitude, NYlongitude)
    LatLng = (nylat_df, nylng_df)
    print("Distance in km between Columbia and " + neighborhood + " is:  " )
    print(distance.distance(Columbia, LatLng).km," kms")
   

Distance in km between Columbia and Hamilton Heights is:  
2.0165162360278153  kms
Distance in km between Columbia and Manhattanville is:  
1.0650302019280105  kms
Distance in km between Columbia and Central Harlem is:  
1.8038495539117967  kms
Distance in km between Columbia and East Harlem is:  
2.2911192832517915  kms
Distance in km between Columbia and Upper West Side is:  
2.595422209139266  kms
Distance in km between Columbia and Midtown is:  
6.147523013104539  kms
Distance in km between Columbia and Morningside Heights is:  
0.17719496689619196  kms
Distance in km between Columbia and Columbia University is:  
0.0  kms


In [65]:
#Import NY Crime Data
import types
import pandas as pd
from botocore.client import Config
import ibm_boto3

def __iter__(self): return 0

# @hidden_cell
# The following code accesses a file in your IBM Cloud Object Storage. It includes your credentials.
# You might want to remove those credentials before you share the notebook.
client_****** = ibm_boto3.client(service_name='s3',
    ibm_api_key_id='laWUQegt0L87NPNfrypYxAOqgbtrN8Nk-_LhkiQGgNK7',
    ibm_auth_endpoint="https://iam.cloud.ibm.com/oidc/token",
    config=Config(signature_version='oauth'),
    endpoint_url='https://s3-api.us-geo.objectstorage.service.networklayer.com')

body = client_*****.get_object(Bucket='courseraibmcapstone-donotdelete-pr-iibp9ibtexxq7g',Key='NYPD_Complaint_Data_Current__Year_To_Date_.csv')['Body']
# add missing __iter__ method, so pandas accepts body as file-like object
if not hasattr(body, "__iter__"): body.__iter__ = types.MethodType( __iter__, body )

NYCrime = pd.read_csv(body)

NYCrime.head(10)

CMPLNT_NUM  ADDR_PCT_CD   BORO_NM CMPLNT_FR_DT    YEAR  Unnamed: 5  \
0   466502077           75  BROOKLYN   2020-03-30  2020.0         NaN   
1   303191835           77  BROOKLYN   2020-03-28  2020.0         NaN   
2   735488557           43     BRONX   2020-03-29  2020.0         NaN   
3   315962428           40     BRONX   2020-03-29  2020.0         NaN   
4   165437868          114    QUEENS   2020-03-27  2020.0         NaN   
5   709032439           45     BRONX   2020-03-27  2020.0         NaN   
6   579248512           42     BRONX   2020-03-27  2020.0         NaN   
7   114545671           71  BROOKLYN   2020-03-25  2020.0         NaN   
8   218043957           44     BRONX   2020-03-25  2020.0         NaN   
9   172952393           47     BRONX   2020-03-23  2020.0         NaN   

   Unnamed: 6 CMPLNT_FR_TM CMPLNT_TO_DT CMPLNT_TO_TM  ... SUSP_SEX  \
0         NaN     17:30:00    3/31/2020      6:53:00  ...      NaN   
1         NaN     19:30:00    3/28/2020     20:30:00  ...        M   
2         NaN     14:10:00          NaN          NaN  ...      NaN   
3         NaN      7:10:00    3/29/2020      7:16:00  ...        M   
4         NaN     13:15:00    3/27/2020     14:00:00  ...      NaN   
5         NaN     10:00:00          NaN          NaN  ...        M   
6         NaN      0:57:00          NaN          NaN  ...        M   
7         NaN     17:55:00    3/25/2020     17:59:00  ...        M   
8         NaN     12:30:00          NaN          NaN  ...        M   
9         NaN     17:00:00          NaN          NaN  ...        M   

  TRANSIT_DISTRICT  VIC_AGE_GROUP        VIC_RACE VIC_SEX  X_COORD_CD  \
0              NaN          25-44           BLACK       M     1018496   
1              NaN            <18         UNKNOWN       F     1003606   
2              NaN        UNKNOWN         UNKNOWN       D     1019853   
3              NaN          25-44  WHITE HISPANIC       F     1007236   
4              NaN          45-64           BLACK       F     1002018   
5              NaN          45-64           WHITE       M     1033699   
6              NaN        UNKNOWN         UNKNOWN       E     1012148   
7              NaN        UNKNOWN         UNKNOWN       E      997851   
8              NaN          18-24           BLACK       M     1003676   
9              NaN          25-44           BLACK       F     1022401   

  Y_COORD_CD   Latitude  Longitude                                   Lat_Lon  
0     178657  40.656991 -73.876574   (40.65699087900003, -73.87657444799999)  
1     185050  40.674583 -73.930222   (40.67458330800008, -73.93022154099998)  
2     241853  40.830443 -73.871349        (40.83044253800006, -73.871349147)  
3     237260  40.817878 -73.916957  (40.817877907000025, -73.91695668199996)  
4     213258  40.752011 -73.935872   (40.75201086000004, -73.93587196099996)  
5     240225  40.825907 -73.821328   (40.82590748600006, -73.82132840799993)  
6     245681  40.840977 -73.899175   (40.84097698500005, -73.89917540299997)  
7     181159  40.663914 -73.950977   (40.66391409200002, -73.95097661399996)  
8     242788  40.833059 -73.929802   (40.83305923900008, -73.92980238799998)  
9     263242  40.889138 -73.862020  (40.889138212000034, -73.86202015999999)  

[10 rows x 38 columns]

In [66]:
# View columns
NYCrime.columns

Index(['CMPLNT_NUM', 'ADDR_PCT_CD', 'BORO_NM', 'CMPLNT_FR_DT', 'YEAR',
       'Unnamed: 5', 'Unnamed: 6', 'CMPLNT_FR_TM', 'CMPLNT_TO_DT',
       'CMPLNT_TO_TM', 'CRM_ATPT_CPTD_CD', 'HADEVELOPT', 'HOUSING_PSA',
       'JURISDICTION_CODE', 'JURIS_DESC', 'KY_CD', 'LAW_CAT_CD',
       'LOC_OF_OCCUR_DESC', 'OFNS_DESC', 'PARKS_NM', 'PATROL_BORO', 'PD_CD',
       'PD_DESC', 'PREM_TYP_DESC', 'RPT_DT', 'STATION_NAME', 'SUSP_AGE_GROUP',
       'SUSP_RACE', 'SUSP_SEX', 'TRANSIT_DISTRICT', 'VIC_AGE_GROUP',
       'VIC_RACE', 'VIC_SEX', 'X_COORD_CD', 'Y_COORD_CD', 'Latitude',
       'Longitude', 'Lat_Lon'],
      dtype='object')

In [67]:

# Clean the NYCrime Data
#Drop columns that are not needed


NYCrime.drop(['CMPLNT_NUM','YEAR', 'Unnamed: 5', 'Unnamed: 6', 'CMPLNT_FR_TM', 'CMPLNT_TO_DT',
       'CMPLNT_TO_TM', 'CRM_ATPT_CPTD_CD', 'HADEVELOPT',
       'HOUSING_PSA', 'JURISDICTION_CODE', 'JURIS_DESC', 'KY_CD', 'LAW_CAT_CD',
       'LOC_OF_OCCUR_DESC', 'RPT_DT', 'PARKS_NM', 'PATROL_BORO', 'PD_CD',
       'PD_DESC', 'PREM_TYP_DESC','KY_CD', 'PD_CD', 'PD_DESC',
       'CRM_ATPT_CPTD_CD', 'LAW_CAT_CD', 'JURIS_DESC',
       'LOC_OF_OCCUR_DESC', 'PREM_TYP_DESC', 'PARKS_NM',
       'HADEVELOPT', 'STATION_NAME', 'SUSP_AGE_GROUP',
       'SUSP_RACE', 'SUSP_SEX', 'TRANSIT_DISTRICT', 'VIC_AGE_GROUP',
       'VIC_RACE', 'VIC_SEX', 'X_COORD_CD', 'Y_COORD_CD'
        ], axis=1, inplace=True)

#Rename columns names for consistency across all dataframes

NYCrime.rename(columns ={'ADDR_PCT_CD' : 'Precinct Number',
                         'CMPLNT_FR_DT': 'Occurrence Year', 
                         'OFNS_DESC' : 'MCI', 
                         'BORO_NM' : 'Borough',
                         'Latitude' : 'Lat', 
                         'Longitude' : 'Long', 
                         'Lat_Lon' : 'Coordinates'}, inplace=True)
#Fix years for dataframe

NYCrime['Occurrence Year'] = pd.to_datetime(NYCrime['Occurrence Year'], format='%Y-%m-%d') #%Y-%m-%d  #%m/%d/%Y

NYCrime['Occurrence Year'] = NYCrime['Occurrence Year'].dt.year 


#Isolate to only the year 2019
NYCrime = NYCrime[NYCrime['Occurrence Year'] == 2019].reset_index(drop=True)


NYCrime.head(5)

Precinct Number    Borough  Occurrence Year              MCI        Lat  \
0                5  MANHATTAN             2019       SEX CRIMES  40.716196   
1               81   BROOKLYN             2019             RAPE  40.689616   
2               83   BROOKLYN             2019  DANGEROUS DRUGS  40.690655   
3               40      BRONX             2019    PETIT LARCENY  40.813805   
4               43      BRONX             2019      THEFT-FRAUD  40.815733   

        Long                               Coordinates  
0 -73.997491  (40.716195914000025, -73.99749074599998)  
1 -73.924393  (40.689615497000034, -73.92439311199998)  
2 -73.908043   (40.69065484200007, -73.90804256199993)  
3 -73.929653   (40.81380495100007, -73.92965290199999)  
4 -73.848350  (40.815733075000026, -73.84835004699994)

In [75]:
#we only want to see only manhattan numbers

NYCrime_Man =NYCrime[NYCrime['Borough'] == 'MANHATTAN'].reset_index(drop=True)

NYCrime_Man.head(10)









Precinct Number    Borough  Occurrence Year                            MCI  \
0                5  MANHATTAN             2019                     SEX CRIMES   
1               23  MANHATTAN             2019  OFF. AGNST PUB ORD SENSBLTY &   
2                5  MANHATTAN             2019                           RAPE   
3                5  MANHATTAN             2019                  PETIT LARCENY   
4                9  MANHATTAN             2019                DANGEROUS DRUGS   
5               18  MANHATTAN             2019                    THEFT-FRAUD   
6               14  MANHATTAN             2019                  GRAND LARCENY   
7               19  MANHATTAN             2019                  GRAND LARCENY   
8               30  MANHATTAN             2019                  PETIT LARCENY   
9               19  MANHATTAN             2019  OFF. AGNST PUB ORD SENSBLTY &   

         Lat       Long                               Coordinates  
0  40.716196 -73.997491  (40.716195914000025, -73.99749074599998)  
1  40.799665 -73.947200  (40.799665264000055, -73.94719977999995)  
2  40.716196 -73.997491  (40.716195914000025, -73.99749074599998)  
3  40.714431 -74.006101  (40.714430898000046, -74.00610127799997)  
4  40.722397 -73.978536   (40.72239709900003, -73.97853584199999)  
5  40.770827 -73.992611  (40.770827222000044, -73.99261118899994)  
6  40.747881 -73.991040   (40.74788104700008, -73.99104019099997)  
7  40.775773 -73.954750   (40.77577282900006, -73.95475034499998)  
8  40.824602 -73.950114   (40.82460236600008, -73.95011391699995)  
9  40.767336 -73.954875   (40.76733554700007, -73.95487521099994)

In [68]:
# Calculate the number of each types of crime or Major Crime Indicator (MCI) for 2019

NYCrimePer = pd.DataFrame(NYCrime['MCI'].value_counts().astype(float))
NYCrimePer = NYCrimePer.reset_index()
NYCrimePer.columns = ['MCI', 'Number of Occurrence in 2019'] 

#convert to percentages 
NYCrimePer['Percentage of Occurrence in 2019'] = 100*NYCrimePer['Number of Occurrence in 2019']/NYCrimePer['Number of Occurrence in 2019'].sum()

#Print to confirm it is as expected

NYCrimePer

MCI  Number of Occurrence in 2019  \
0                     PETIT LARCENY                        1171.0   
1                     GRAND LARCENY                        1104.0   
2                     HARRASSMENT 2                         512.0   
3    CRIMINAL MISCHIEF & RELATED OF                         466.0   
4     OFF. AGNST PUB ORD SENSBLTY &                         339.0   
5                       THEFT-FRAUD                         280.0   
6                        SEX CRIMES                         190.0   
7      ASSAULT 3 & RELATED OFFENSES                         153.0   
8           MISCELLANEOUS PENAL LAW                         135.0   
9                              RAPE                          96.0   
10                         BURGLARY                          80.0   
11                           FRAUDS                          80.0   
12    UNAUTHORIZED USE OF A VEHICLE                          77.0   
13                  DANGEROUS DRUGS                          71.0   
14                   FELONY ASSAULT                          65.0   
15   GRAND LARCENY OF MOTOR VEHICLE                          58.0   
16   OFFENSES AGAINST PUBLIC ADMINI                          45.0   
17                          FORGERY                          43.0   
18     NYS LAWS-UNCLASSIFIED FELONY                          31.0   
19              ADMINISTRATIVE CODE                          20.0   
20                          ROBBERY                          15.0   
21                            ARSON                          15.0   
22                CRIMINAL TRESPASS                          13.0   
23         VEHICLE AND TRAFFIC LAWS                          11.0   
24      OFFENSES AGAINST THE PERSON                           9.0   
25    POSSESSION OF STOLEN PROPERTY                           9.0   
26   OTHER OFFENSES RELATED TO THEF                           9.0   
27                THEFT OF SERVICES                           7.0   
28                DANGEROUS WEAPONS                           7.0   
29   OTHER STATE LAWS (NON PENAL LA                           5.0   
30  MURDER & NON-NEGL. MANSLAUGHTER                           5.0   
31            ANTICIPATORY OFFENSES                           3.0   
32   INTOXICATED & IMPAIRED DRIVING                           3.0   
33         OFFENSES INVOLVING FRAUD                           2.0   
34             FRAUDULENT ACCOSTING                           2.0   
35  PROSTITUTION & RELATED OFFENSES                           2.0   

    Percentage of Occurrence in 2019  
0                          22.813170  
1                          21.507890  
2                           9.974674  
3                           9.078512  
4                           6.604325  
5                           5.454900  
6                           3.701539  
7                           2.980713  
8                           2.630041  
9                           1.870251  
10                          1.558543  
11                          1.558543  
12                          1.500097  
13                          1.383207  
14                          1.266316  
15                          1.129944  
16                          0.876680  
17                          0.837717  
18                          0.603935  
19                          0.389636  
20                          0.292227  
21                          0.292227  
22                          0.253263  
23                          0.214300  
24                          0.175336  
25                          0.175336  
26                          0.175336  
27                          0.136372  
28                          0.136372  
29                          0.097409  
30                          0.097409  
31                          0.058445  
32                          0.058445  
33                          0.038964  
34                          0.038964  
35                          0.038964

In [69]:
#visualize data

!wget -q -O 'police_precincts.geojson' https://raw.githubusercontent.com/dwillis/nyc-maps/master/police_precincts.geojson
print('Data downloaded!')







Data downloaded!


In [71]:
#import json
file = open('police_precincts.geojson', 'rt')
#print(file.readlines())

NYCrime_geo = json.load(file)




In [72]:


#calculate the total number of incidences per neighborhood
#Lat, Long columns
NY_crime = pd.DataFrame(NYCrime['Precinct Number'].value_counts().astype(float))
NY_crime = NY_crime.reset_index()

#NYCrime = NYCrime[NYCrime['Precinct Number'] < 35].reset_index(drop=True)

#NYCrime.head(5)
NY_crime.columns = ['Precinct Number', 'Number of Incidents']
NY_crime.head(10)









Precinct Number  Number of Incidents
0               75                156.0
1               19                155.0
2              113                136.0
3               70                111.0
4              105                110.0
5               67                107.0
6               18                100.0
7               44                100.0
8               14                100.0
9              114                 98.0

In [73]:

#create a choropleth map of precint locations and the relative intensity of the crimes
NYCrime_map = folium.Map(location=[NYlatitude, NYlongitude], zoom_start=12,  tiles='openstreetmap')
NYCrime_map.choropleth(
    geo_data = NYCrime_geo,
    name = 'NYC Crime Heat Map',
    data = NY_crime,
    columns = ['Precinct Number', 'Number of Incidents'],
    key_on = 'feature.properties.Precinct',
    zoome_start = 5,
    fill_color = 'BuPu',
    fill_opacity = 0.7,
    line_opacity = 0.2,
    legend_name = 'Crimes in New York City - Manhattan'
)

for lat, lng, borough, neighborhood in zip(NY_df['Latitude'], NY_df['Longitude'], NY_df['Borough'], NY_df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(NYCrime_map)



NYCrime_map

In [82]:
CLIENT_ID = 'CLIENT' # your Foursquare ID
CLIENT_SECRET = 'SECRET' # your Foursquare Secret
VERSION = '20181201' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: CLIENT
CLIENT_SECRET:SECRET


In [76]:

def getNearbyVenues(names, latitudes, longitudes, radius=1000, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng,            
            v['venue']['name'], 
            v['venue']['id'],
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Location', 
                  'Location Latitude', 
                  'Location Longitude', 
                  'Venue',
                  'Venue id',                
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category'        
                   ]
    
    return(nearby_venues)





In [20]:
#(NY_df['Latitude'], NY_df['Longitude'], NY_df['Borough'], NY_df['Neighborhood']


Manhattan_data_venues = getNearbyVenues(names=NY_df['Neighborhood'],
                                   latitudes=NY_df['Latitude'],
                                   longitudes=NY_df['Longitude']
                                  )







Hamilton Heights
Manhattanville
Central Harlem
East Harlem
Upper West Side
Midtown
Morningside Heights
Columbia University


In [21]:
#test to see if harlem is still here

NY_df



Borough         Neighborhood   Latitude  Longitude
0  Manhattan     Hamilton Heights  40.823604 -73.949688
1  Manhattan       Manhattanville  40.816934 -73.957385
2  Manhattan       Central Harlem  40.815976 -73.943211
3  Manhattan          East Harlem  40.792249 -73.944182
4  Manhattan      Upper West Side  40.787658 -73.977059
5  Manhattan              Midtown  40.754691 -73.981669
6  Manhattan  Morningside Heights  40.808000 -73.963896
7  Manhattan  Columbia University  40.807949 -73.961797

In [22]:

print(Manhattan_data_venues.shape)








(800, 8)


In [23]:



print('There are {} unique venue categories.'.format(len(Manhattan_data_venues['Venue Category'].unique())))
univen = Manhattan_data_venues.groupby('Location').nunique('Venue Category')
univen

There are 165 unique venue categories.


Location  Location Latitude  Location Longitude  Venue  \
Location                                                                      
Central Harlem              1                  1                   1    100   
Columbia University         1                  1                   1     99   
East Harlem                 1                  1                   1    100   
Hamilton Heights            1                  1                   1    100   
Manhattanville              1                  1                   1    100   
Midtown                     1                  1                   1     96   
Morningside Heights         1                  1                   1     99   
Upper West Side             1                  1                   1    100   

                     Venue id  Venue Latitude  Venue Longitude  Venue Category  
Location                                                                        
Central Harlem            100             100              100              63  
Columbia University       100             100              100              57  
East Harlem               100             100              100              56  
Hamilton Heights          100             100              100              61  
Manhattanville            100             100              100              66  
Midtown                   100             100              100              64  
Morningside Heights       100             100              100              58  
Upper West Side           100             100              100              59

In [24]:


Manhattan_data_venues.groupby('Venue Category').nunique()




Location  Location Latitude  \
Venue Category                                               
Accessories Store                     1                  1   
African Restaurant                    4                  4   
American Restaurant                   8                  8   
Arepa Restaurant                      1                  1   
Art Gallery                           3                  3   
Art Museum                            2                  2   
Arts & Crafts Store                   3                  3   
Asian Restaurant                      1                  1   
BBQ Joint                             2                  2   
Bagel Shop                            5                  5   
Bakery                                6                  6   
Bank                                  2                  2   
Bar                                   4                  4   
Beer Bar                              2                  2   
Bike Trail                            1                  1   
Bookstore                             5                  5   
Boutique                              4                  4   
Boxing Gym                            1                  1   
Breakfast Spot                        1                  1   
Buffet                                1                  1   
Building                              1                  1   
Burger Joint                          4                  4   
Cafeteria                             1                  1   
Café                                  7                  7   
Caribbean Restaurant                  2                  2   
Chinese Restaurant                    8                  8   
Chocolate Shop                        1                  1   
Church                                1                  1   
Climbing Gym                          2                  2   
Clothing Store                        2                  2   
...                                 ...                ...   
State / Provincial Park               2                  2   
Steakhouse                            2                  2   
Street Art                            1                  1   
Supermarket                           2                  2   
Sushi Restaurant                      7                  7   
Szechuan Restaurant                   1                  1   
TV Station                            1                  1   
Taco Place                            3                  3   
Tailor Shop                           1                  1   
Tapas Restaurant                      1                  1   
Tea Room                              1                  1   
Tennis Court                          5                  5   
Thai Restaurant                       4                  4   
Theater                               5                  5   
Tiki Bar                              1                  1   
Toy / Game Store                      2                  2   
Track                                 2                  2   
Trail                                 1                  1   
Train Station                         1                  1   
Turkish Restaurant                    1                  1   
Vegetarian / Vegan Restaurant         2                  2   
Video Game Store                      1                  1   
Vietnamese Restaurant                 2                  2   
Waterfront                            1                  1   
Whisky Bar                            3                  3   
Wine Bar                              5                  5   
Wine Shop                             6                  6   
Wings Joint                           1                  1   
Women's Store                         1                  1   
Yoga Studio                           6                  6   

                               Location Longitude  Venue  Venue id  \
Venue Category                                        

In [25]:
# one hot encoding
M_onehot = pd.get_dummies(Manhattan_data_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighbourhood column back to dataframe
M_onehot['Location'] = Manhattan_data_venues['Location'] 

# move neighbourhood column to the first column
fixed_columns = [M_onehot.columns[-1]] + list(M_onehot.columns[:-1])
M_onehot = M_onehot[fixed_columns]

M_onehot.head()

Location  Accessories Store  African Restaurant  \
0  Hamilton Heights                  0                   0   
1  Hamilton Heights                  0                   0   
2  Hamilton Heights                  0                   0   
3  Hamilton Heights                  0                   0   
4  Hamilton Heights                  0                   0   

   American Restaurant  Arepa Restaurant  Art Gallery  Art Museum  \
0                    0                 0            0           0   
1                    0                 0            0           0   
2                    0                 0            0           0   
3                    0                 0            0           0   
4                    0                 0            0           0   

   Arts & Crafts Store  Asian Restaurant  BBQ Joint  ...  \
0                    0                 0          0  ...   
1                    0                 0          0  ...   
2                    0                 0          0  ...   
3                    0                 0          0  ...   
4                    0                 0          0  ...   

   Vegetarian / Vegan Restaurant  Video Game Store  Vietnamese Restaurant  \
0                              0                 0                      0   
1                              0                 0                      0   
2                              0                 0                      0   
3                              0                 0                      0   
4                              0                 0                      0   

   Waterfront  Whisky Bar  Wine Bar  Wine Shop  Wings Joint  Women's Store  \
0           0           0         0          0            0              0   
1           0           0         0          0            0              0   
2           0           0         0          0            0              0   
3           0           0         1          0            0              0   
4           0           0         0          0            0              0   

   Yoga Studio  
0            0  
1            0  
2            0  
3            0  
4            1  

[5 rows x 166 columns]

In [26]:
M_onehot.shape

(800, 166)

In [27]:
M_grouped = M_onehot.groupby('Location').mean().reset_index()
M_grouped

Location  Accessories Store  African Restaurant  \
0       Central Harlem               0.00                0.04   
1  Columbia University               0.00                0.01   
2          East Harlem               0.00                0.01   
3     Hamilton Heights               0.00                0.01   
4       Manhattanville               0.00                0.00   
5              Midtown               0.00                0.00   
6  Morningside Heights               0.00                0.00   
7      Upper West Side               0.01                0.00   

   American Restaurant  Arepa Restaurant  Art Gallery  Art Museum  \
0                 0.03              0.00         0.01        0.01   
1                 0.04              0.00         0.00        0.00   
2                 0.01              0.00         0.00        0.02   
3                 0.03              0.01         0.00        0.00   
4                 0.04              0.00         0.02        0.00   
5                 0.03              0.00         0.01        0.00   
6                 0.05              0.00         0.00        0.00   
7                 0.03              0.00         0.00        0.00   

   Arts & Crafts Store  Asian Restaurant  BBQ Joint  ...  \
0                 0.02              0.00       0.01  ...   
1                 0.00              0.00       0.00  ...   
2                 0.00              0.00       0.00  ...   
3                 0.00              0.00       0.00  ...   
4                 0.01              0.00       0.01  ...   
5                 0.00              0.00       0.00  ...   
6                 0.00              0.00       0.00  ...   
7                 0.01              0.01       0.00  ...   

   Vegetarian / Vegan Restaurant  Video Game Store  Vietnamese Restaurant  \
0                           0.00              0.00                   0.00   
1                           0.00              0.00                   0.00   
2                           0.00              0.00                   0.00   
3                           0.00              0.00                   0.00   
4                           0.00              0.00                   0.00   
5                           0.01              0.01                   0.01   
6                           0.00              0.00                   0.01   
7                           0.02              0.00                   0.00   

   Waterfront  Whisky Bar  Wine Bar  Wine Shop  Wings Joint  Women's Store  \
0        0.00        0.00      0.00       0.02         0.00           0.00   
1        0.00        0.01      0.01       0.02         0.00           0.00   
2        0.00        0.00      0.01       0.01         0.00           0.00   
3        0.00        0.01      0.01       0.00         0.00           0.00   
4        0.00        0.00      0.00       0.02         0.00           0.00   
5        0.00        0.00      0.00       0.00         0.00           0.02   
6        0.00        0.01      0.01       0.02         0.01           0.00   
7        0.01        0.00      0.03       0.01         0.00           0.00   

   Yoga Studio  
0         0.02  
1         0.00  
2         0.00  
3         0.03  
4         0.01  
5         0.01  
6         0.01  
7         0.02  

[8 rows x 166 columns]

In [28]:
M_grouped.shape

(8, 166)

In [29]:
num_top_venues = 5

for hood in M_grouped['Location']:
    print("----"+hood+"----")
    temp = M_grouped[M_grouped['Location'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Central Harlem----
                             venue  freq
0  Southern / Soul Food Restaurant  0.05
1                             Café  0.04
2               African Restaurant  0.04
3               Seafood Restaurant  0.03
4                French Restaurant  0.03


----Columbia University----
                 venue  freq
0          Coffee Shop  0.07
1                 Park  0.06
2   Italian Restaurant  0.05
3  American Restaurant  0.04
4   Chinese Restaurant  0.04


----East Harlem----
                venue  freq
0  Mexican Restaurant  0.07
1                Café  0.06
2              Bakery  0.06
3     Thai Restaurant  0.04
4       Deli / Bodega  0.04


----Hamilton Heights----
                venue  freq
0         Coffee Shop  0.06
1                Park  0.04
2                Café  0.04
3                 Bar  0.04
4  Mexican Restaurant  0.04


----Manhattanville----
                 venue  freq
0                 Park  0.06
1   Italian Restaurant  0.05
2  American Restaurant  0.04
3

In [77]:

def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [78]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Location']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
location_venues_sorted = pd.DataFrame(columns=columns)
location_venues_sorted['Location'] = M_grouped['Location']

for ind in np.arange(M_grouped.shape[0]):
    location_venues_sorted.iloc[ind, 1:] = return_most_common_venues(M_grouped.iloc[ind, :], num_top_venues)

location_venues_sorted

Location            1st Most Common Venue 2nd Most Common Venue  \
0       Central Harlem  Southern / Soul Food Restaurant                  Café   
1  Columbia University                      Coffee Shop                  Park   
2          East Harlem               Mexican Restaurant                Bakery   
3     Hamilton Heights                      Coffee Shop    Mexican Restaurant   
4       Manhattanville                             Park    Italian Restaurant   
5              Midtown                          Theater                 Plaza   
6  Morningside Heights                      Coffee Shop                  Park   
7      Upper West Side               Italian Restaurant                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    African Restaurant      Sushi Restaurant          Cocktail Bar   
1    Italian Restaurant    Seafood Restaurant    Chinese Restaurant   
2                  Café       Thai Restaurant         Deli / Bodega   
3                   Bar                  Café                  Park   
4   American Restaurant    Seafood Restaurant    Mexican Restaurant   
5            Steakhouse           Coffee Shop                 Hotel   
6    Italian Restaurant   American Restaurant    Chinese Restaurant   
7                  Park                   Gym           Coffee Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                Lounge                   Bar    Seafood Restaurant   
1   American Restaurant    Mexican Restaurant                Bakery   
2           Pizza Place    Italian Restaurant                   Gym   
3           Yoga Studio   American Restaurant      Sushi Restaurant   
4                  Café           Coffee Shop          Cocktail Bar   
5        Sandwich Place   American Restaurant          Gourmet Shop   
6         Grocery Store    Mexican Restaurant            Playground   
7        Ice Cream Shop          Dessert Shop                   Bar   

  9th Most Common Venue           10th Most Common Venue  
0           Pizza Place              American Restaurant  
1            Playground                        Bookstore  
2                 Plaza                         Fountain  
3  Ethiopian Restaurant  Southern / Soul Food Restaurant  
4     Indian Restaurant                     Tennis Court  
5   Japanese Restaurant                 Sushi Restaurant  
6    Seafood Restaurant                        Bookstore  
7              Wine Bar                           Bakery

In [32]:
# set number of clusters
kclusters = 5

M_grouped_clustering = M_grouped.drop('Location', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(M_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([0, 3, 2, 0, 0, 1, 3, 4], dtype=int32)

In [33]:
M_merged = NY_df
M_merged.rename(columns={'Neighborhood': 'Location'}, inplace=True)
M_merged.sort_values(by='Location', inplace=True)
M_merged




Borough             Location   Latitude  Longitude
2  Manhattan       Central Harlem  40.815976 -73.943211
7  Manhattan  Columbia University  40.807949 -73.961797
3  Manhattan          East Harlem  40.792249 -73.944182
0  Manhattan     Hamilton Heights  40.823604 -73.949688
1  Manhattan       Manhattanville  40.816934 -73.957385
5  Manhattan              Midtown  40.754691 -73.981669
6  Manhattan  Morningside Heights  40.808000 -73.963896
4  Manhattan      Upper West Side  40.787658 -73.977059

In [34]:

# add clustering labels
M_merged['Cluster Labels'] = kmeans.labels_ #this was changed from kmeans.labels_
M_merged

M_merged = M_merged.merge(location_venues_sorted, left_on='Location', right_on='Location')
M_merged


Borough             Location   Latitude  Longitude  Cluster Labels  \
0  Manhattan       Central Harlem  40.815976 -73.943211               0   
1  Manhattan  Columbia University  40.807949 -73.961797               3   
2  Manhattan          East Harlem  40.792249 -73.944182               2   
3  Manhattan     Hamilton Heights  40.823604 -73.949688               0   
4  Manhattan       Manhattanville  40.816934 -73.957385               0   
5  Manhattan              Midtown  40.754691 -73.981669               1   
6  Manhattan  Morningside Heights  40.808000 -73.963896               3   
7  Manhattan      Upper West Side  40.787658 -73.977059               4   

             1st Most Common Venue 2nd Most Common Venue  \
0  Southern / Soul Food Restaurant                  Café   
1                      Coffee Shop                  Park   
2               Mexican Restaurant                Bakery   
3                      Coffee Shop    Mexican Restaurant   
4                             Park    Italian Restaurant   
5                          Theater                 Plaza   
6                      Coffee Shop                  Park   
7               Italian Restaurant                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0    African Restaurant      Sushi Restaurant          Cocktail Bar   
1    Italian Restaurant    Seafood Restaurant    Chinese Restaurant   
2                  Café       Thai Restaurant         Deli / Bodega   
3                   Bar                  Café                  Park   
4   American Restaurant    Seafood Restaurant    Mexican Restaurant   
5            Steakhouse           Coffee Shop                 Hotel   
6    Italian Restaurant   American Restaurant    Chinese Restaurant   
7                  Park                   Gym           Coffee Shop   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                Lounge                   Bar    Seafood Restaurant   
1   American Restaurant    Mexican Restaurant                Bakery   
2           Pizza Place    Italian Restaurant                   Gym   
3           Yoga Studio   American Restaurant      Sushi Restaurant   
4                  Café           Coffee Shop          Cocktail Bar   
5        Sandwich Place   American Restaurant          Gourmet Shop   
6         Grocery Store    Mexican Restaurant            Playground   
7        Ice Cream Shop          Dessert Shop                   Bar   

  9th Most Common Venue           10th Most Common Venue  
0           Pizza Place              American Restaurant  
1            Playground                        Bookstore  
2                 Plaza                         Fountain  
3  Ethiopian Restaurant  Southern / Soul Food Restaurant  
4     Indian Restaurant                     Tennis Court  
5   Japanese Restaurant                 Sushi Restaurant  
6    Seafood Restaurant                        Bookstore  
7              Wine Bar                           Bakery

In [41]:




# create map
map_clusters = folium.Map(location=[NYlatitude, NYlongitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(M_merged['Latitude'], M_merged['Longitude'], M_merged['Location'], M_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker([lat, lon], radius=10,popup=label,color=rainbow[cluster-1],fill=True,fill_color=rainbow[cluster-1],
        fill_opacity=0.5).add_to(map_clusters)
map_clusters




In [81]:
NYCrime_map = folium.Map(location=[NYlatitude, NYlongitude], zoom_start=14, tiles='openstreetmap')
NYCrime_map.choropleth(
    geo_data = NYCrime_geo,
    name = 'NYC Crime Heat Map',
    data = NY_crime,
    columns = ['Precinct Number', 'Number of Incidents'],
    key_on = 'feature.properties.Precinct',
    zoome_start = 10,
    fill_color = 'BuPu',
    fill_opacity = 0.7,
    line_opacity = 0.2,
    legend_name = 'Crimes in New York City - Manhattan'
)

for lat, lng, borough, neighborhood in zip(NY_df['Latitude'], NY_df['Longitude'], NY_df['Borough'], NY_df['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(NYCrime_map)


ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(M_merged['Latitude'], M_merged['Longitude'], M_merged['Location'], M_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker([lat, lon], radius=10,popup=label,color=rainbow[cluster-1],fill=True,fill_color=rainbow[cluster-1],
        fill_opacity=0.5).add_to(NYCrime_map)
    
NYCrime_map









